# Semester Project
##### Jeff Sharpe, Rachel Pullen, Jackie Woodlief

We are trying to figure out if loans are actually given to people who need it!

Step 1: How do you tell if someone needs a loan or not?

Use the downloaded dataset to fit a ML alg and test on KIVA data sets

Look at loan data in Pakistan and reasons why people need those loans!

In [1]:
# Import statements! Are loans given to people who actually need it, 3 more files, contain poverty index of every country

import numpy as np
import pandas as pd
from sklearn.preprocessing import LabelEncoder, Imputer

In [2]:
loans = pd.read_csv("data-science-for-good-kiva-crowdfunding/kiva_loans.csv")
mpi_locations = pd.read_csv("data-science-for-good-kiva-crowdfunding/kiva_mpi_region_locations.csv")
loan_theme_id = pd.read_csv("data-science-for-good-kiva-crowdfunding/loan_theme_ids.csv")
loan_theme_region = pd.read_csv("data-science-for-good-kiva-crowdfunding/loan_themes_by_region.csv")
country_stats = pd.read_csv("data-science-for-good-kiva-crowdfunding/country_stats.csv")

In [3]:
pak_table_stats = country_stats.loc[country_stats['country_name'] == "Pakistan"]
pak_table_stats

country_name country_code country_code3 continent         region  \
3     Pakistan           PK           PAK      Asia  Southern Asia   

   population  population_below_poverty_line       hdi  life_expectancy  \
3   197015955                           29.5  0.550354           66.365   

   expected_years_of_schooling  mean_years_of_schooling          gni  \
3                      8.10691                  5.08946  5031.173074   

  kiva_country_name  
3          Pakistan

In [4]:
country_stats.head(5)

country_name country_code country_code3 continent           region  \
0        India           IN           IND      Asia    Southern Asia   
1      Nigeria           NG           NGA    Africa   Western Africa   
2       Mexico           MX           MEX  Americas  Central America   
3     Pakistan           PK           PAK      Asia    Southern Asia   
4   Bangladesh           BD           BGD      Asia    Southern Asia   

   population  population_below_poverty_line       hdi  life_expectancy  \
0  1339180127                           21.9  0.623559           68.322   
1   190886311                           70.0  0.527105           53.057   
2   129163276                           46.2  0.761683           76.972   
3   197015955                           29.5  0.550354           66.365   
4   164669751                           31.5  0.578824           71.985   

   expected_years_of_schooling  mean_years_of_schooling           gni  \
0                    11.696590                 6.298834   5663.474799   
1                     9.970482                 6.000000   5442.901264   
2                    13.299090                 8.554985  16383.106680   
3                     8.106910                 5.089460   5031.173074   
4                    10.178706                 5.241577   3341.490722   

  kiva_country_name  
0             India  
1           Nigeria  
2            Mexico  
3          Pakistan  
4        Bangladesh

In [5]:
loans["sector"].value_counts() #15 unique sectors!!

Agriculture       180302
Food              136657
Retail            124494
Services           45140
Personal Use       36385
Housing            33731
Clothing           32742
Education          31013
Transportation     15518
Arts               12060
Health              9223
Construction        6268
Manufacturing       6208
Entertainment        830
Wholesale            634
Name: sector, dtype: int64

In [6]:
loans.filter(like='22', axis = 0)

id  funded_amount  loan_amount                   activity  \
22       653050          575.0        575.0             Clothing Sales   
122      653346          200.0        200.0        Fruits & Vegetables   
220      653379          800.0        800.0         Education provider   
221      653282          125.0        125.0                  Tailoring   
222      653232         2400.0       2400.0              Grocery Store   
223      653156         2125.0       2125.0               Animal Sales   
224      653197          250.0        250.0                    Farming   
225      653243          250.0        250.0               Beauty Salon   
226      653152         4175.0       4175.0               Butcher Shop   
227      653255         2500.0       2500.0               Beauty Salon   
228      653292         1700.0       1700.0      Food Production/Sales   
229      653309          250.0        250.0                 Food Stall   
322      653184         1200.0       1200.0               Construction   
422      653606          850.0        850.0                       Food   
522      653575          250.0        250.0      Food Production/Sales   
622      653726          600.0        600.0                Auto Repair   
722      653801          500.0        500.0                     Retail   
822      653951          475.0        475.0                Barber Shop   
922      654184          125.0        125.0              Used Clothing   
1022     654314          300.0        300.0                     Crafts   
1122     654119          325.0        325.0        Fruits & Vegetables   
1220     653961          225.0        225.0              General Store   
1221     654138          150.0        150.0  Personal Housing Expenses   
1222     654308          800.0        800.0                  Livestock   
1223     654285          300.0        300.0      Food Production/Sales   
1224     654182          125.0        125.0             Clothing Sales   
1225     654231         1400.0       1400.0             Clothing Sales   
1226     654259         1000.0       1000.0  Personal Housing Expenses   
1227     654043         1100.0       1175.0              Grocery Store   
1228     654396         1600.0       1600.0                Paper Sales   
...         ...            ...          ...                        ...   
669228  1334891           50.0       1200.0          Motorcycle Repair   
669229  1334884          100.0        100.0               Celebrations   
669322  1335281           50.0        650.0                     Sewing   
669422  1335251            0.0       2200.0             Clothing Sales   
669522  1335250          350.0        350.0                     Retail   
669622  1334484          300.0        300.0              Grocery Store   
669722  1334805           75.0        575.0                    Farming   
669822  1335231            0.0        225.0                 Food Stall   
669922  1335932            0.0       5775.0              General Store   
670022  1336136           75.0        325.0                    Farming   
670122  1336142          875.0        875.0                     Retail   
670220  1335406          350.0        700.0    Personal Products Sales   
670221  1336052         1075.0       1075.0                     Crafts   
670222  1336172         1100.0       1100.0                     Retail   
670223  1335940            0.0        425.0                     Retail   
670224  1335870          125.0        300.0               Animal Sales   
670225  1335528            0.0        875.0                    Cereals   
670226  1336065            0.0        600.0              General Store   
670227  1335960         1000.0       1000.0                 Restaurant   
670228  1336211            0.0       1100.0              General Store   
670229  1335843           50.0        300.0                 Embroidery   
670322  1335395          100.0        100.0                    Farming   
670422  1336180  

In [7]:
# Look at the regions within a country and compare

pak_table = loans.loc[loans['country'] == "Pakistan"]
pak_table

id  funded_amount  loan_amount                      activity  \
0        653051          300.0        300.0           Fruits & Vegetables   
1        653053          575.0        575.0                      Rickshaw   
3        653063          200.0        200.0                    Embroidery   
4        653084          400.0        400.0                    Milk Sales   
7        653078          400.0        400.0                  Beauty Salon   
8        653082          475.0        475.0                 Manufacturing   
9        653048          625.0        625.0         Food Production/Sales   
10       653060          200.0        200.0                      Rickshaw   
11       653088          400.0        400.0                     Wholesale   
12       653089          400.0        400.0                 General Store   
13       653062          400.0        400.0                Clothing Sales   
15       653054          300.0        300.0                      Rickshaw   
16       653091          400.0        400.0                 General Store   
17       653052          875.0        875.0                     Tailoring   
19       653080          475.0        475.0                  Beauty Salon   
20       653065          250.0        250.0                        Bakery   
21       653055          350.0        350.0                    Restaurant   
22       653050          575.0        575.0                Clothing Sales   
23       653079          350.0        350.0                    Embroidery   
24       653061          250.0        250.0                    Food Stall   
27       653056          475.0        475.0                      Rickshaw   
30       653059          250.0        250.0                Clothing Sales   
31       653087          400.0        400.0                 Manufacturing   
32       653076          450.0        450.0                 General Store   
34       653086          400.0        400.0                    Milk Sales   
35       653047         2225.0       2225.0       Personal Products Sales   
36       653058          400.0        400.0                      Services   
37       653083          475.0        475.0                        Sewing   
38       653057          350.0        350.0           Home Products Sales   
39       653090          475.0        475.0                 General Store   
...         ...            ...          ...                           ...   
670276  1335826           50.0        475.0                     Recycling   
670299  1335833           50.0        250.0          Motorcycle Transport   
670327  1335510            0.0        300.0                 General Store   
670344  1335824            0.0        250.0                    Embroidery   
670350  1335851          250.0        250.0                        Crafts   
670364  1335638           50.0        200.0                      Rickshaw   
670393  1335813           50.0        575.0                     Tailoring   
670401  1335836          150.0        350.0                    Embroidery   
670415  1335848           50.0        200.0                        Retail   
670457  1336327            0.0        250.0                    Embroidery   
670462  1336326            0.0        300.0                    Embroidery   
670474  1336316            0.0        475.0                    Embroidery   
670484  1336245            0.0        200.0                Clothing Sales   
670486  1336249            0.0        300.0  Cloth & Dressmaking Supplies   
670499  1336324            0.0        475.0                    Embroidery   
670508  1336261            0.0        300.0                Clothing Sales   
670514  1336259            0.0        300.0                      Rickshaw   
670515  1336331            0.0        300.0                    Embroidery   
670516  1336253            0.0        300.0           Home Products Sales   
670522  1336329            0.0        475.0                    Embroidery   
670526  1

In [8]:
#Look at regions within Pakistan

pak_table["region"].value_counts()

Lahore                 7178
Rawalpindi             4496
Multan                 2526
Gujranwala             1466
Haripur                1186
Abbottabad              893
Gujrat                  814
Sialkot                 733
Mansehra                514
Oghi                    401
Muzaffargarh            360
Faisalabad              319
Hafizabad               279
Bahawalpur              239
Sahiwal                 230
Jhang                   229
Layyah                  210
Rahim Yar Khan          185
Karachi                 173
Pakpatan                171
Mandi Bahauddin         170
Okara                   152
Sheikhupura             132
Kot Addu                130
Jahanian                127
Kabeerwala              116
Wazirabad               104
Mian Chanoon             97
Lodhran                  96
Sargodha                 96
                       ... 
Chishtian                 2
Dera Sardaran             2
Dijikot                   2
Hasil Pur                 2
Gharo               

In [9]:
loans.head()

id  funded_amount  loan_amount             activity          sector  \
0  653051          300.0        300.0  Fruits & Vegetables            Food   
1  653053          575.0        575.0             Rickshaw  Transportation   
2  653068          150.0        150.0       Transportation  Transportation   
3  653063          200.0        200.0           Embroidery            Arts   
4  653084          400.0        400.0           Milk Sales            Food   

                                                 use country_code   country  \
0            To buy seasonal, fresh fruits to sell.            PK  Pakistan   
1  to repair and maintain the auto rickshaw used ...           PK  Pakistan   
2  To repair their old cycle-van and buy another ...           IN     India   
3  to purchase an embroidery machine and a variet...           PK  Pakistan   
4                           to purchase one buffalo.           PK  Pakistan   

         region currency  partner_id                posted_time  \
0        Lahore      PKR       247.0  2014-01-01 06:12:39+00:00   
1        Lahore      PKR       247.0  2014-01-01 06:51:08+00:00   
2     Maynaguri      INR       334.0  2014-01-01 09:58:07+00:00   
3        Lahore      PKR       247.0  2014-01-01 08:03:11+00:00   
4  Abdul Hakeem      PKR       245.0  2014-01-01 11:53:19+00:00   

              disbursed_time                funded_time  term_in_months  \
0  2013-12-17 08:00:00+00:00  2014-01-02 10:06:32+00:00            12.0   
1  2013-12-17 08:00:00+00:00  2014-01-02 09:17:23+00:00            11.0   
2  2013-12-17 08:00:00+00:00  2014-01-01 16:01:36+00:00            43.0   
3  2013-12-24 08:00:00+00:00  2014-01-01 13:00:00+00:00            11.0   
4  2013-12-17 08:00:00+00:00  2014-01-01 19:18:51+00:00            14.0   

   lender_count                          tags borrower_genders  \
0            12                           NaN           female   
1            14                           NaN   female, female   
2             6  user_favorite, user_favorite           female   
3             8                           NaN           female   
4            16                           NaN           female   

  repayment_interval        date  
0          irregular  2014-01-01  
1          irregular  2014-01-01  
2             bullet  2014-01-01  
3          irregular  2014-01-01  
4            monthly  2014-01-01

In [10]:
pak_table_mpi_loc = mpi_locations.loc[mpi_locations['country'] == "Pakistan"]
pak_table_mpi_loc

LocationName  ISO   country              region  \
733              Punjab, Pakistan  PAK  Pakistan              Punjab   
734               Sindh, Pakistan  PAK  Pakistan               Sindh   
735  Khyber Pakhtunkhwa, Pakistan  PAK  Pakistan  Khyber Pakhtunkhwa   
736         Balochistan, Pakistan  PAK  Pakistan         Balochistan   
737    Gilgit Baltistan, Pakistan  PAK  Pakistan    Gilgit Baltistan   
738     Islamabad (ICT), Pakistan  PAK  Pakistan     Islamabad (ICT)   

    world_region    MPI                              geo        lat        lon  
733   South Asia  0.184         (31.1704063, 72.7097161)  31.170406  72.709716  
734   South Asia  0.294  (25.8943018, 68.52471489999999)  25.894302  68.524715  
735   South Asia  0.247          (34.9526205, 72.331113)  34.952621  72.331113  
736   South Asia  0.402         (28.4907332, 65.0957792)  28.490733  65.095779  
737   South Asia  0.233  (35.80256670000001, 74.9831808)  35.802567  74.983181  
738   South Asia  0.039         (33.7293882, 73.0931461)  33.729388  73.093146

In [11]:
mpi_locations.head() #MPI is the poverty index!!

LocationName  ISO      country      region world_region    MPI  \
0  Badakhshan, Afghanistan  AFG  Afghanistan  Badakhshan   South Asia  0.387   
1     Badghis, Afghanistan  AFG  Afghanistan     Badghis   South Asia  0.466   
2     Baghlan, Afghanistan  AFG  Afghanistan     Baghlan   South Asia  0.300   
3       Balkh, Afghanistan  AFG  Afghanistan       Balkh   South Asia  0.301   
4      Bamyan, Afghanistan  AFG  Afghanistan      Bamyan   South Asia  0.325   

                               geo        lat        lon  
0  (36.7347725, 70.81199529999999)  36.734772  70.811995  
1         (35.1671339, 63.7695384)  35.167134  63.769538  
2         (35.8042947, 69.2877535)  35.804295  69.287754  
3         (36.7550603, 66.8975372)  36.755060  66.897537  
4         (34.8100067, 67.8212104)  34.810007  67.821210

In [12]:
loan_theme_id.head() # Maybe come back to this? If we need to

id    Loan Theme ID          Loan Theme Type  Partner ID
0  638631  a1050000000skGl                  General       151.0
1  640322  a1050000000skGl                  General       151.0
2  641006  a1050000002X1ij         Higher Education       160.0
3  641019  a1050000002X1ij         Higher Education       160.0
4  641594  a1050000002VbsW  Subsistence Agriculture       336.0

In [13]:
loan_theme_id["Loan Theme Type"].value_counts()

General                                           380693
Underserved                                        62575
Agriculture                                        40108
Rural Inclusion                                    21228
Water                                              20131
Higher Education                                   17728
General (Women)                                    16566
Vulnerable Populations                             16354
Green                                              13913
Water and Sanitation                               12032
Startup                                             9887
Subsistence Agriculture and Solar Lanterns          8597
Youth                                               8444
Subsistence Agriculture                             8247
Vulnerable Women                                    8184
FUSAI                                               6014
Extreme Poverty                                     5475
Murabaha                       

In [14]:
loan_theme_region["sector"].value_counts()

General Financial Inclusion    13679
Clean Energy                     840
Other                            338
Agriculture                      300
Mobile Money and ICT             210
Education                        143
Water and Sanitation              92
Artisan                           55
DSE Direct                        45
SME Financial Inclusion           32
Health                             2
Name: sector, dtype: int64

In [15]:
loan_theme_region.head() #rural percentage, KEEP

Partner ID               Field Partner Name                       sector  \
0           9  KREDIT Microfinance Institution  General Financial Inclusion   
1           9  KREDIT Microfinance Institution  General Financial Inclusion   
2           9  KREDIT Microfinance Institution  General Financial Inclusion   
3           9  KREDIT Microfinance Institution  General Financial Inclusion   
4           9  KREDIT Microfinance Institution  General Financial Inclusion   

     Loan Theme ID         Loan Theme Type   country forkiva  \
0  a1050000000slfi        Higher Education  Cambodia      No   
1  a10500000068jPe  Vulnerable Populations  Cambodia      No   
2  a1050000000slfi        Higher Education  Cambodia      No   
3  a10500000068jPe  Vulnerable Populations  Cambodia      No   
4  a1050000002X1Uu              Sanitation  Cambodia      No   

                  region     geocode_old  ISO    ...     amount  \
0       Banteay Meanchey  (13.75, 103.0)  KHM    ...        450   
1    Battambang Province             NaN  KHM    ...      20275   
2    Battambang Province             NaN  KHM    ...       9150   
3  Kampong Cham Province   (12.0, 105.5)  KHM    ...     604950   
4  Kampong Cham Province   (12.0, 105.5)  KHM    ...        275   

                      LocationName                      geocode  \
0       Banteay Meanchey, Cambodia  [(13.6672596, 102.8975098)]   
1    Battambang Province, Cambodia   [(13.0286971, 102.989615)]   
2    Battambang Province, Cambodia   [(13.0286971, 102.989615)]   
3  Kampong Cham Province, Cambodia  [(12.0982918, 105.3131185)]   
4  Kampong Cham Province, Cambodia  [(12.0982918, 105.3131185)]   

                                 names                        geo        lat  \
0  Banteay Meanchey Province; Cambodia  (13.6672596, 102.8975098)  13.667260   
1        Battambang Province; Cambodia   (13.0286971, 102.989615)  13.028697   
2        Battambang Province; Cambodia   (13.0286971, 102.989615)  13.028697   
3      Kampong Cham Province; Cambodia  (12.0982918, 105.3131185)  12.098292   
4      Kampong Cham Province; Cambodia  (12.0982918, 105.3131185)  12.098292   

          lon                   mpi_region                    mpi_geo  \
0  102.897510  Banteay Mean Chey, Cambodia  (13.6672596, 102.8975098)   
1  102.989615  Banteay Mean Chey, Cambodia  (13.6672596, 102.8975098)   
2  102.989615  Banteay Mean Chey, Cambodia  (13.6672596, 102.8975098)   
3  105.313119       Kampong Cham, Cambodia  (11.9924294, 105.4645408)   
4  105.313119       Kampong Cham, Cambodia  (11.9924294, 105.4645408)   

  rural_pct  
0      90.0  
1      90.0  
2      90.0  
3      90.0  
4      90.0  

[5 rows x 21 columns]

In [16]:
loan_theme_region["geocode"][5]

'[(12.0982918, 105.3131185)]'

In [17]:
loan_theme_region["geocode"][5].split(',')

['[(12.0982918', ' 105.3131185)]']

In [18]:
loan_theme_region["geocode"][5].split(',')[1]

' 105.3131185)]'

In [19]:
loan_theme_region["lat"][3]

12.0982918

# Working on loans.csv

The next blocks we will be doing work on loans.csv to get it ready for ml algorithms! More specifically the pak_table that we created earlier!

In [20]:
pak_table

id  funded_amount  loan_amount                      activity  \
0        653051          300.0        300.0           Fruits & Vegetables   
1        653053          575.0        575.0                      Rickshaw   
3        653063          200.0        200.0                    Embroidery   
4        653084          400.0        400.0                    Milk Sales   
7        653078          400.0        400.0                  Beauty Salon   
8        653082          475.0        475.0                 Manufacturing   
9        653048          625.0        625.0         Food Production/Sales   
10       653060          200.0        200.0                      Rickshaw   
11       653088          400.0        400.0                     Wholesale   
12       653089          400.0        400.0                 General Store   
13       653062          400.0        400.0                Clothing Sales   
15       653054          300.0        300.0                      Rickshaw   
16       653091          400.0        400.0                 General Store   
17       653052          875.0        875.0                     Tailoring   
19       653080          475.0        475.0                  Beauty Salon   
20       653065          250.0        250.0                        Bakery   
21       653055          350.0        350.0                    Restaurant   
22       653050          575.0        575.0                Clothing Sales   
23       653079          350.0        350.0                    Embroidery   
24       653061          250.0        250.0                    Food Stall   
27       653056          475.0        475.0                      Rickshaw   
30       653059          250.0        250.0                Clothing Sales   
31       653087          400.0        400.0                 Manufacturing   
32       653076          450.0        450.0                 General Store   
34       653086          400.0        400.0                    Milk Sales   
35       653047         2225.0       2225.0       Personal Products Sales   
36       653058          400.0        400.0                      Services   
37       653083          475.0        475.0                        Sewing   
38       653057          350.0        350.0           Home Products Sales   
39       653090          475.0        475.0                 General Store   
...         ...            ...          ...                           ...   
670276  1335826           50.0        475.0                     Recycling   
670299  1335833           50.0        250.0          Motorcycle Transport   
670327  1335510            0.0        300.0                 General Store   
670344  1335824            0.0        250.0                    Embroidery   
670350  1335851          250.0        250.0                        Crafts   
670364  1335638           50.0        200.0                      Rickshaw   
670393  1335813           50.0        575.0                     Tailoring   
670401  1335836          150.0        350.0                    Embroidery   
670415  1335848           50.0        200.0                        Retail   
670457  1336327            0.0        250.0                    Embroidery   
670462  1336326            0.0        300.0                    Embroidery   
670474  1336316            0.0        475.0                    Embroidery   
670484  1336245            0.0        200.0                Clothing Sales   
670486  1336249            0.0        300.0  Cloth & Dressmaking Supplies   
670499  1336324            0.0        475.0                    Embroidery   
670508  1336261            0.0        300.0                Clothing Sales   
670514  1336259            0.0        300.0                      Rickshaw   
670515  1336331            0.0        300.0                    Embroidery   
670516  1336253            0.0        300.0           Home Products Sales   
670522  1336329            0.0        475.0                    Embroidery   
670526  1

In [21]:
# copy_pak_table["borrower_genders"].value_counts()

NameError: name 'copy_pak_table' is not defined

In [ ]:
# copy_pak_table.info()

In [22]:
# First, lets get a copy of it so that we can always have the original unaltered

copy_pak_table = pd.DataFrame.copy(pak_table)
copy_pak_table

id  funded_amount  loan_amount                      activity  \
0        653051          300.0        300.0           Fruits & Vegetables   
1        653053          575.0        575.0                      Rickshaw   
3        653063          200.0        200.0                    Embroidery   
4        653084          400.0        400.0                    Milk Sales   
7        653078          400.0        400.0                  Beauty Salon   
8        653082          475.0        475.0                 Manufacturing   
9        653048          625.0        625.0         Food Production/Sales   
10       653060          200.0        200.0                      Rickshaw   
11       653088          400.0        400.0                     Wholesale   
12       653089          400.0        400.0                 General Store   
13       653062          400.0        400.0                Clothing Sales   
15       653054          300.0        300.0                      Rickshaw   
16       653091          400.0        400.0                 General Store   
17       653052          875.0        875.0                     Tailoring   
19       653080          475.0        475.0                  Beauty Salon   
20       653065          250.0        250.0                        Bakery   
21       653055          350.0        350.0                    Restaurant   
22       653050          575.0        575.0                Clothing Sales   
23       653079          350.0        350.0                    Embroidery   
24       653061          250.0        250.0                    Food Stall   
27       653056          475.0        475.0                      Rickshaw   
30       653059          250.0        250.0                Clothing Sales   
31       653087          400.0        400.0                 Manufacturing   
32       653076          450.0        450.0                 General Store   
34       653086          400.0        400.0                    Milk Sales   
35       653047         2225.0       2225.0       Personal Products Sales   
36       653058          400.0        400.0                      Services   
37       653083          475.0        475.0                        Sewing   
38       653057          350.0        350.0           Home Products Sales   
39       653090          475.0        475.0                 General Store   
...         ...            ...          ...                           ...   
670276  1335826           50.0        475.0                     Recycling   
670299  1335833           50.0        250.0          Motorcycle Transport   
670327  1335510            0.0        300.0                 General Store   
670344  1335824            0.0        250.0                    Embroidery   
670350  1335851          250.0        250.0                        Crafts   
670364  1335638           50.0        200.0                      Rickshaw   
670393  1335813           50.0        575.0                     Tailoring   
670401  1335836          150.0        350.0                    Embroidery   
670415  1335848           50.0        200.0                        Retail   
670457  1336327            0.0        250.0                    Embroidery   
670462  1336326            0.0        300.0                    Embroidery   
670474  1336316            0.0        475.0                    Embroidery   
670484  1336245            0.0        200.0                Clothing Sales   
670486  1336249            0.0        300.0  Cloth & Dressmaking Supplies   
670499  1336324            0.0        475.0                    Embroidery   
670508  1336261            0.0        300.0                Clothing Sales   
670514  1336259            0.0        300.0                      Rickshaw   
670515  1336331            0.0        300.0                    Embroidery   
670516  1336253            0.0        300.0           Home Products Sales   
670522  1336329            0.0        475.0                    Embroidery   
670526  1

In [23]:
# Lets create an instance of the LabelEncoder()

encoder = LabelEncoder()

In [24]:
sector_cat = copy_pak_table["sector"]
activity_cat = copy_pak_table["activity"]
region_cat = copy_pak_table["region"]
gender_cat = copy_pak_table["borrower_genders"]
repay_cat = copy_pak_table["repayment_interval"]

In [25]:
# There were some missing values here, so instead of deleting the entire row of data we decided to fill them with 
# an other category that we create

region_cat = region_cat.fillna('Other Region')
gender_cat = region_cat.fillna('Other Gender')

In [26]:
# Now let's encode some of the text attributes that will be important for the future, such as sector and activity

sector_encode = encoder.fit_transform(sector_cat)
activity_encode = encoder.fit_transform(activity_cat)
region_encode = encoder.fit_transform(region_cat)
gender_encode = encoder.fit_transform(gender_cat)
repay_encode = encoder.fit_transform(repay_cat)

In [27]:
sector_encode

array([ 6, 13,  1, ...,  0,  0,  0])

In [28]:
gender_encode

array([78, 78, 78, ...,  6,  6,  6])

In [29]:
copy_pak_table["sector"] = sector_encode
copy_pak_table["activity"] = activity_encode
copy_pak_table["region"] = region_encode
copy_pak_table["borrower_genders"] = gender_encode
copy_pak_table["repayment_interval"] = repay_encode

In [30]:
copy_pak_table["currency"].value_counts()

PKR    26856
USD        1
Name: currency, dtype: int64

In [31]:
copy_pak_table["date"].value_counts()

2017-06-23    147
2016-12-21    135
2017-06-20    125
2016-07-26     99
2016-12-27     97
2016-05-26     96
2016-09-23     93
2017-02-28     92
2017-03-13     92
2016-11-24     91
2014-12-17     89
2017-06-19     89
2017-02-16     89
2017-05-18     87
2017-02-17     86
2016-04-26     86
2016-11-23     86
2017-01-26     85
2017-01-20     84
2017-02-20     84
2016-07-15     83
2017-02-24     82
2017-02-15     81
2016-10-25     81
2017-03-22     81
2016-01-28     79
2017-01-13     78
2017-03-20     78
2016-07-18     77
2014-02-19     76
             ... 
2016-02-08      3
2014-09-21      2
2014-07-07      2
2016-04-07      2
2015-09-12      2
2017-07-21      2
2016-12-24      2
2014-08-24      2
2017-01-15      2
2015-06-01      2
2017-06-29      2
2017-07-20      1
2016-08-20      1
2016-12-18      1
2015-02-03      1
2014-09-01      1
2016-04-23      1
2017-04-07      1
2017-01-07      1
2015-10-18      1
2014-07-03      1
2016-09-24      1
2017-03-19      1
2017-06-28      1
2017-01-09

In [32]:
copy_pak_table.head()

id  funded_amount  loan_amount  activity  sector  \
0  653051          300.0        300.0        55       6   
1  653053          575.0        575.0       111      13   
3  653063          200.0        200.0        43       1   
4  653084          400.0        400.0        79       6   
7  653078          400.0        400.0         7      12   

                                                 use country_code   country  \
0            To buy seasonal, fresh fruits to sell.            PK  Pakistan   
1  to repair and maintain the auto rickshaw used ...           PK  Pakistan   
3  to purchase an embroidery machine and a variet...           PK  Pakistan   
4                           to purchase one buffalo.           PK  Pakistan   
7         to buy more hair and skin care products.             PK  Pakistan   

   region currency  partner_id                posted_time  \
0      78      PKR       247.0  2014-01-01 06:12:39+00:00   
1      78      PKR       247.0  2014-01-01 06:51:08+00:00   
3      78      PKR       247.0  2014-01-01 08:03:11+00:00   
4       1      PKR       245.0  2014-01-01 11:53:19+00:00   
7      30      PKR       245.0  2014-01-01 11:46:01+00:00   

              disbursed_time                funded_time  term_in_months  \
0  2013-12-17 08:00:00+00:00  2014-01-02 10:06:32+00:00            12.0   
1  2013-12-17 08:00:00+00:00  2014-01-02 09:17:23+00:00            11.0   
3  2013-12-24 08:00:00+00:00  2014-01-01 13:00:00+00:00            11.0   
4  2013-12-17 08:00:00+00:00  2014-01-01 19:18:51+00:00            14.0   
7  2013-12-20 08:00:00+00:00  2014-01-10 18:18:44+00:00            14.0   

   lender_count                        tags  borrower_genders  \
0            12                         NaN                78   
1            14                         NaN                78   
3             8                         NaN                78   
4            16                         NaN                 1   
7             8  #Elderly, #Woman Owned Biz                30   

   repayment_interval        date  
0                   1  2014-01-01  
1                   1  2014-01-01  
3                   1  2014-01-01  
4                   2  2014-01-01  
7                   2  2014-01-01

In [33]:
# Now that we have encoded the various categories we can drop some columns that are repetitive or maybe not
# so important, for example, every currency except for one instance is PKR

copy_pak_table = copy_pak_table.drop("country_code", 1)
copy_pak_table = copy_pak_table.drop("country", 1)
copy_pak_table = copy_pak_table.drop("currency", 1)
copy_pak_table = copy_pak_table.drop("tags", 1)
copy_pak_table = copy_pak_table.drop("use", 1)
# copy_pak_table = copy_pak_table.drop()
# copy_pak_table = copy_pak_table.drop()
# copy_pak_table = copy_pak_table.drop()
# copy_pak_table = copy_pak_table.drop()

In [34]:
copy_pak_table["borrower_genders"].value_counts()

78     7178
123    4496
95     2526
39     1466
43     1186
0       893
40      814
134     733
88      514
103     401
98      360
31      319
41      279
9       239
126     230
52      229
80      210
118     185
59      173
106     171
86      170
104     152
132     132
73      130
49      127
56      116
144     104
92       97
130      96
82       96
       ... 
26        2
46        2
137       2
85        2
91        2
2         2
34        2
12        2
28        2
100       2
20        2
121       2
110       1
27        1
102       1
7         1
74        1
16        1
97        1
133       1
101       1
131       1
129       1
14        1
141       1
93        1
44        1
116       1
84        1
25        1
Name: borrower_genders, Length: 146, dtype: int64

In [35]:
copy_pak_table.head(3)

id  funded_amount  loan_amount  activity  sector  region  partner_id  \
0  653051          300.0        300.0        55       6      78       247.0   
1  653053          575.0        575.0       111      13      78       247.0   
3  653063          200.0        200.0        43       1      78       247.0   

                 posted_time             disbursed_time  \
0  2014-01-01 06:12:39+00:00  2013-12-17 08:00:00+00:00   
1  2014-01-01 06:51:08+00:00  2013-12-17 08:00:00+00:00   
3  2014-01-01 08:03:11+00:00  2013-12-24 08:00:00+00:00   

                 funded_time  term_in_months  lender_count  borrower_genders  \
0  2014-01-02 10:06:32+00:00            12.0            12                78   
1  2014-01-02 09:17:23+00:00            11.0            14                78   
3  2014-01-01 13:00:00+00:00            11.0             8                78   

   repayment_interval        date  
0                   1  2014-01-01  
1                   1  2014-01-01  
3                   1  2014-01-01

In [36]:
copy_pak_table["day"] = 0
copy_pak_table["month"] = 0
copy_pak_table["year"] = 0

In [37]:
copy_pak_table["date"][1]

'2014-01-01'

In [38]:
test = copy_pak_table["date"][0].split('-')
test

['2014', '01', '01']

In [39]:
len(copy_pak_table)

26857

In [ ]:
# Here we are separating the date into an easier format to use for our machine learning process
# we are splitting the single column into three columns, one for day, year and month!

for k in range(0, copy_pak_table.index[-1]):
    
    try:
        year, month, day = copy_pak_table["date"][k].split('-')
        copy_pak_table["year"][k] = year
        copy_pak_table["month"][k] = month
        copy_pak_table["day"][k] = day
    except KeyError:
        print("There was a key error")   

/home/shelob/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/home/shelob/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':
/home/shelob/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  # Remove the CWD from sys.path while we load stuff.


There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was 

There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was 

There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was 

There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was 

...

There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was 

There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was 

There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was 

There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was 

There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was a key error
There was 

In [ ]:
# Just testing this function!

copy_pak_table.index[-1]

In [ ]:
copy_pak_table.head(20)

In [ ]:
# Now we can go ahead and delete the date column

copy_pak_table = copy_pak_table.drop("date", 1)
copy_pak_table = copy_pak_table.drop("posted_time", 1)
copy_pak_table = copy_pak_table.drop("disbursed_time", 1)
copy_pak_table = copy_pak_table.drop("funded_time", 1)


In [ ]:
imputer = Imputer(strategy = "median")

In [ ]:
imputer.fit(copy_pak_table)
X = imputer.transform(copy_pak_table)
transform_pak = pd.DataFrame(X, columns = copy_pak_table.columns)
transform_pak